In [1]:
import matplotlib as mpl
import matplotlib.pyplot as plt
%matplotlib inline
import numpy as np
import sklearn
import pandas as pd
import os
import sys
import time
import tensorflow as tf

from tensorflow import keras

In [3]:
physical_devices = tf.config.experimental.list_physical_devices('GPU')
assert len(physical_devices) > 0, "Not enough GPU hardware devices available"
tf.config.experimental.set_memory_growth(physical_devices[0], True)

## 导入数据集

In [4]:
input_dir="datasets"
df_data = pd.read_csv(os.path.join(input_dir, "train"+".csv"))
df_label = pd.read_csv(os.path.join(input_dir, "valid"+".csv"), header=None)

In [5]:
x_train_all, y_train_all = df_data, df_label

## 数据分析与处理

In [6]:
x_valid, x_train = x_train_all.to_numpy().reshape(-1,2,7)[:5000], x_train_all.to_numpy().reshape(-1,2,7)[5000:]
y_valid, y_train = y_train_all.to_numpy()[:5000], y_train_all.to_numpy()[5000:]
x_test, y_test = x_train_all.to_numpy().reshape(-1,2,7),y_train_all.to_numpy()
print(x_valid.shape, y_valid.shape)
print(x_train.shape, y_train.shape)
print(np.max(x_train), np.min(x_train))


(5000, 2, 7) (5000, 1)
(21607, 2, 7) (21607, 1)
6882.0 0.9


In [7]:
print(x_valid[0])

[[492.6 383.  252.7 436.8 570.  390.3 434.1]
 [967.1 555.5 297.7 413.4 459.5 392.2 609.7]]


In [8]:
# x = (x - u) / std

from sklearn.preprocessing import StandardScaler

scaler = StandardScaler()
# x_train: [None, 1,14] -> [None, 7,7]
x_train_scaled = scaler.fit_transform(
    x_train.astype(np.float32).reshape(-1, 1)).reshape(-1,2,7,1)
x_valid_scaled = scaler.transform(
    x_valid.astype(np.float32).reshape(-1, 1)).reshape(-1,2,7,1)
x_test_scaled = scaler.transform(
    x_test.astype(np.float32).reshape(-1, 1)).reshape(-1,2,7,1)
print(np.max(x_train_scaled), np.min(x_train_scaled))

29.378624 -0.92783993


## 建立模型并训练

In [9]:
def build_model(hidden_layers = 1,
                layer_size = 30,
                learning_rate = 3e-3):
    model = keras.models.Sequential()
    model.add(keras.layers.Conv2D(filters=8, kernel_size=3,
                              padding='same',
                              activation='selu',
                              input_shape=(2, 7, 1)))
    model.add(keras.layers.SeparableConv2D(filters=16, kernel_size=3,
                                       padding='same',
                                       activation='selu'))
    model.add(keras.layers.MaxPool2D(pool_size=2))
    model.add(keras.layers.Flatten())
    model.add(keras.layers.Dense(128, activation='selu'))
    model.add(keras.layers.Dense(32,activation='selu'))
    for _ in range(hidden_layers - 1):
        model.add(keras.layers.Dense(layer_size,
                                     activation = 'relu'))
    model.add(keras.layers.Dense(1,activation='sigmoid'))
    optimizer = keras.optimizers.SGD(learning_rate)
    model.compile(loss = 'binary_crossentropy', optimizer = optimizer,metrics = ["accuracy",tf.keras.metrics.AUC()])
    return model

sklearn_model = keras.wrappers.scikit_learn.KerasRegressor(
    build_fn = build_model)


In [ ]:
from scipy.stats import reciprocal
# f(x) = 1/(x*log(b/a)) a <= x <= b

param_distribution = {
    "hidden_layers":[1, 2, 3, 4],
    "layer_size": np.arange(1, 100),
    "learning_rate": reciprocal(1e-4, 1e-2),
}

from sklearn.model_selection import RandomizedSearchCV
callbacks = [keras.callbacks.EarlyStopping(patience=5, min_delta=1e-2)]
random_search_cv = RandomizedSearchCV(sklearn_model,
                                      param_distribution,
                                      n_iter = 10,
                                      cv = 3,
                                      n_jobs = 1)
random_search_cv.fit(x_train_scaled, y_train, epochs = 30,
                     validation_data = (x_valid_scaled, y_valid),
                     callbacks = callbacks)

# cross_validation: 训练集分成n份，n-1训练，最后一份验证.

Train on 14404 samples, validate on 5000 samples
Epoch 1/30
14404/14404 [==============================] - 3s 200us/sample - loss: 0.6272 - accuracy: 0.6939 - auc_2: 0.7409 - val_loss: 0.5532 - val_accuracy: 0.7688 - val_auc_2: 0.8168
Epoch 2/30
14404/14404 [==============================] - 2s 120us/sample - loss: 0.5063 - accuracy: 0.7796 - auc_2: 0.8464 - val_loss: 0.4738 - val_accuracy: 0.7856 - val_auc_2: 0.8591
Epoch 3/30
14404/14404 [==============================] - 2s 120us/sample - loss: 0.4454 - accuracy: 0.8049 - auc_2: 0.8796 - val_loss: 0.4304 - val_accuracy: 0.8120 - val_auc_2: 0.8853
Epoch 4/30
14404/14404 [==============================] - 2s 120us/sample - loss: 0.4116 - accuracy: 0.8246 - auc_2: 0.8968 - val_loss: 0.4069 - val_accuracy: 0.8222 - val_auc_2: 0.8976
Epoch 5/30
14404/14404 [==============================] - 2s 121us/sample - loss: 0.3915 - accuracy: 0.8339 - auc_2: 0.9058 - val_loss: 0.3892 - val_accuracy: 0.8364 - val_auc_2: 0.9054
Epoch 6/30
14404/1440

Train on 14405 samples, validate on 5000 samples
Epoch 1/30
14405/14405 [==============================] - 3s 202us/sample - loss: 0.6693 - accuracy: 0.6435 - auc_3: 0.6278 - val_loss: 0.6227 - val_accuracy: 0.6996 - val_auc_3: 0.7489
Epoch 2/30
14405/14405 [==============================] - 2s 120us/sample - loss: 0.5849 - accuracy: 0.7277 - auc_3: 0.7911 - val_loss: 0.5528 - val_accuracy: 0.7368 - val_auc_3: 0.8112
Epoch 3/30
14405/14405 [==============================] - 2s 121us/sample - loss: 0.5254 - accuracy: 0.7509 - auc_3: 0.8304 - val_loss: 0.5058 - val_accuracy: 0.7592 - val_auc_3: 0.8386
Epoch 4/30
14405/14405 [==============================] - 2s 121us/sample - loss: 0.4801 - accuracy: 0.7825 - auc_3: 0.8597 - val_loss: 0.4620 - val_accuracy: 0.7924 - val_auc_3: 0.8699
Epoch 5/30
14405/14405 [==============================] - 2s 120us/sample - loss: 0.4373 - accuracy: 0.8148 - auc_3: 0.8863 - val_loss: 0.4238 - val_accuracy: 0.8184 - val_auc_3: 0.8916
Epoch 6/30
14405/1440

Train on 14405 samples, validate on 5000 samples
Epoch 1/30
14405/14405 [==============================] - 3s 211us/sample - loss: 0.6294 - accuracy: 0.6918 - auc_4: 0.7552 - val_loss: 0.5661 - val_accuracy: 0.7692 - val_auc_4: 0.8211
Epoch 2/30
14405/14405 [==============================] - 2s 121us/sample - loss: 0.5288 - accuracy: 0.7687 - auc_4: 0.8270 - val_loss: 0.4969 - val_accuracy: 0.7724 - val_auc_4: 0.8421
Epoch 3/30
14405/14405 [==============================] - 2s 121us/sample - loss: 0.4797 - accuracy: 0.7820 - auc_4: 0.8538 - val_loss: 0.4619 - val_accuracy: 0.7882 - val_auc_4: 0.8645
Epoch 4/30
14405/14405 [==============================] - 2s 120us/sample - loss: 0.4463 - accuracy: 0.7994 - auc_4: 0.8759 - val_loss: 0.4295 - val_accuracy: 0.8064 - val_auc_4: 0.8866
Epoch 5/30
14405/14405 [==============================] - 2s 120us/sample - loss: 0.4181 - accuracy: 0.8190 - auc_4: 0.8930 - val_loss: 0.4056 - val_accuracy: 0.8244 - val_auc_4: 0.9010
Epoch 6/30
14405/1440

Train on 14404 samples, validate on 5000 samples
Epoch 1/30
14404/14404 [==============================] - 3s 221us/sample - loss: 0.6878 - accuracy: 0.6538 - auc_5: 0.7761 - val_loss: 0.6869 - val_accuracy: 0.6966 - val_auc_5: 0.7962
Epoch 2/30
14404/14404 [==============================] - 2s 131us/sample - loss: 0.6854 - accuracy: 0.7503 - auc_5: 0.8128 - val_loss: 0.6844 - val_accuracy: 0.7746 - val_auc_5: 0.8209
Epoch 3/30
14404/14404 [==============================] - 2s 130us/sample - loss: 0.6830 - accuracy: 0.7910 - auc_5: 0.8295 - val_loss: 0.6819 - val_accuracy: 0.7942 - val_auc_5: 0.8296
Epoch 4/30
14404/14404 [==============================] - 2s 131us/sample - loss: 0.6806 - accuracy: 0.7921 - auc_5: 0.8408 - val_loss: 0.6796 - val_accuracy: 0.7892 - val_auc_5: 0.8394
Epoch 5/30
14404/14404 [==============================] - 2s 129us/sample - loss: 0.6783 - accuracy: 0.7806 - auc_5: 0.8463 - val_loss: 0.6774 - val_accuracy: 0.7758 - val_auc_5: 0.8442
Epoch 6/30
14404/1440

Train on 14405 samples, validate on 5000 samples
Epoch 1/30
14405/14405 [==============================] - 3s 224us/sample - loss: 0.6980 - accuracy: 0.3829 - auc_6: 0.3404 - val_loss: 0.6955 - val_accuracy: 0.4136 - val_auc_6: 0.3729
Epoch 2/30
14405/14405 [==============================] - 2s 133us/sample - loss: 0.6937 - accuracy: 0.4623 - auc_6: 0.4283 - val_loss: 0.6916 - val_accuracy: 0.5170 - val_auc_6: 0.5249
Epoch 3/30
14405/14405 [==============================] - 2s 132us/sample - loss: 0.6896 - accuracy: 0.6145 - auc_6: 0.6347 - val_loss: 0.6877 - val_accuracy: 0.6464 - val_auc_6: 0.7096
Epoch 4/30
14405/14405 [==============================] - 2s 132us/sample - loss: 0.6855 - accuracy: 0.6822 - auc_6: 0.7606 - val_loss: 0.6839 - val_accuracy: 0.6830 - val_auc_6: 0.7722
Epoch 5/30
14405/14405 [==============================] - 2s 133us/sample - loss: 0.6816 - accuracy: 0.6983 - auc_6: 0.7915 - val_loss: 0.6804 - val_accuracy: 0.7010 - val_auc_6: 0.7882
Epoch 6/30
14405/1440

...

Train on 14405 samples, validate on 5000 samples
Epoch 1/30
14405/14405 [==============================] - 3s 200us/sample - loss: 0.6489 - accuracy: 0.6596 - auc_27: 0.7700 - val_loss: 0.5946 - val_accuracy: 0.7820 - val_auc_27: 0.8418
Epoch 2/30
14405/14405 [==============================] - 2s 127us/sample - loss: 0.5315 - accuracy: 0.7894 - auc_27: 0.8530 - val_loss: 0.4736 - val_accuracy: 0.8010 - val_auc_27: 0.8684
Epoch 3/30
14405/14405 [==============================] - 2s 127us/sample - loss: 0.4410 - accuracy: 0.8102 - auc_27: 0.8832 - val_loss: 0.4191 - val_accuracy: 0.8180 - val_auc_27: 0.8929
Epoch 4/30
14405/14405 [==============================] - 2s 126us/sample - loss: 0.3997 - accuracy: 0.8292 - auc_27: 0.9011 - val_loss: 0.3997 - val_accuracy: 0.8272 - val_auc_27: 0.9025
Epoch 5/30
14405/14405 [==============================] - 2s 126us/sample - loss: 0.3772 - accuracy: 0.8436 - auc_27: 0.9112 - val_loss: 0.3735 - val_accuracy: 0.8440 - val_auc_27: 0.9135
Epoch 6/30


Train on 14405 samples, validate on 5000 samples
Epoch 1/30
14405/14405 [==============================] - 3s 224us/sample - loss: 0.6538 - accuracy: 0.6479 - auc_28: 0.7001 - val_loss: 0.5995 - val_accuracy: 0.7380 - val_auc_28: 0.8079
Epoch 2/30
14405/14405 [==============================] - 2s 125us/sample - loss: 0.5465 - accuracy: 0.7596 - auc_28: 0.8319 - val_loss: 0.5018 - val_accuracy: 0.7718 - val_auc_28: 0.8566
Epoch 3/30
14405/14405 [==============================] - 2s 126us/sample - loss: 0.4662 - accuracy: 0.7879 - auc_28: 0.8716 - val_loss: 0.4406 - val_accuracy: 0.8072 - val_auc_28: 0.8843
Epoch 4/30
14405/14405 [==============================] - 2s 125us/sample - loss: 0.4118 - accuracy: 0.8245 - auc_28: 0.8985 - val_loss: 0.3968 - val_accuracy: 0.8360 - val_auc_28: 0.9053
Epoch 5/30
14405/14405 [==============================] - 2s 125us/sample - loss: 0.3815 - accuracy: 0.8457 - auc_28: 0.9098 - val_loss: 0.3746 - val_accuracy: 0.8396 - val_auc_28: 0.9130
Epoch 6/30


Train on 14404 samples, validate on 5000 samples
Epoch 1/30
14404/14404 [==============================] - 3s 207us/sample - loss: 0.6908 - accuracy: 0.5627 - auc_29: 0.5047 - val_loss: 0.6884 - val_accuracy: 0.5704 - val_auc_29: 0.5000
Epoch 2/30
14404/14404 [==============================] - 2s 129us/sample - loss: 0.6878 - accuracy: 0.5639 - auc_29: 0.5106 - val_loss: 0.6859 - val_accuracy: 0.5704 - val_auc_29: 0.5000
Epoch 3/30
14404/14404 [==============================] - 2s 129us/sample - loss: 0.6863 - accuracy: 0.5639 - auc_29: 0.5044 - val_loss: 0.6847 - val_accuracy: 0.5704 - val_auc_29: 0.5000
Epoch 4/30
14404/14404 [==============================] - 2s 129us/sample - loss: 0.6856 - accuracy: 0.5639 - auc_29: 0.4970 - val_loss: 0.6841 - val_accuracy: 0.5704 - val_auc_29: 0.5000
Epoch 5/30
14404/14404 [==============================] - 2s 129us/sample - loss: 0.6853 - accuracy: 0.5639 - auc_29: 0.5028 - val_loss: 0.6838 - val_accuracy: 0.5704 - val_auc_29: 0.5000
Epoch 6/30


Train on 14405 samples, validate on 5000 samples
Epoch 1/30
14405/14405 [==============================] - 3s 208us/sample - loss: 0.6911 - accuracy: 0.5593 - auc_30: 0.4934 - val_loss: 0.6887 - val_accuracy: 0.5704 - val_auc_30: 0.5000
Epoch 2/30
14405/14405 [==============================] - 2s 135us/sample - loss: 0.6885 - accuracy: 0.5598 - auc_30: 0.5025 - val_loss: 0.6864 - val_accuracy: 0.5704 - val_auc_30: 0.5000
Epoch 3/30
14405/14405 [==============================] - 2s 129us/sample - loss: 0.6872 - accuracy: 0.5598 - auc_30: 0.4949 - val_loss: 0.6852 - val_accuracy: 0.5704 - val_auc_30: 0.5000
Epoch 4/30
14405/14405 [==============================] - 2s 128us/sample - loss: 0.6866 - accuracy: 0.5598 - auc_30: 0.4988 - val_loss: 0.6845 - val_accuracy: 0.5704 - val_auc_30: 0.5000
Epoch 5/30
14405/14405 [==============================] - 2s 127us/sample - loss: 0.6863 - accuracy: 0.5598 - auc_30: 0.4946 - val_loss: 0.6841 - val_accuracy: 0.5704 - val_auc_30: 0.5000
Epoch 6/30


Train on 14405 samples, validate on 5000 samples
Epoch 1/30
14405/14405 [==============================] - 3s 234us/sample - loss: 0.6909 - accuracy: 0.5622 - auc_31: 0.4965 - val_loss: 0.6885 - val_accuracy: 0.5704 - val_auc_31: 0.5000
Epoch 2/30
14405/14405 [==============================] - 2s 129us/sample - loss: 0.6880 - accuracy: 0.5625 - auc_31: 0.5011 - val_loss: 0.6861 - val_accuracy: 0.5704 - val_auc_31: 0.5000
Epoch 3/30
14405/14405 [==============================] - 2s 129us/sample - loss: 0.6867 - accuracy: 0.5625 - auc_31: 0.4920 - val_loss: 0.6849 - val_accuracy: 0.5704 - val_auc_31: 0.5000
Epoch 4/30
14405/14405 [==============================] - 2s 128us/sample - loss: 0.6860 - accuracy: 0.5625 - auc_31: 0.5003 - val_loss: 0.6843 - val_accuracy: 0.5704 - val_auc_31: 0.5000
Epoch 5/30
14405/14405 [==============================] - 2s 129us/sample - loss: 0.6856 - accuracy: 0.5625 - auc_31: 0.4987 - val_loss: 0.6839 - val_accuracy: 0.5704 - val_auc_31: 0.5000
Epoch 6/30


In [ ]:
print(random_search_cv.best_params_)
print(random_search_cv.best_score_)
print(random_search_cv.best_estimator_)

In [ ]:
def plot_learning_curves(history):
    pd.DataFrame(history.history).plot(figsize=(8, 5))
    plt.grid(True)
    plt.gca().set_ylim(0, 1)
    plt.show()

plot_learning_curves(history)

In [ ]:
model = random_search_cv.best_estimator_.model
model.evaluate(x_test_scaled, y_test)